# Wellness in Toronto: IBM Applied Data Science Capstone

### by Joshua Kehler

In partial fullfillment of IBM Data Science Professional Certificate offered by Coursera

## Determine the optimal location for a new wellness center in Toronto, Canada

### (1) Import Libraries 

In [2]:
import pandas as pd # library for data analysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import numpy as np # library to handle data in a vectorized manner
import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents
import os
from sklearn.cluster import KMeans # import k-means from clustering stage

!conda install -c conda-forge folium=0.5.0 --yes
import folium 
from geopy.geocoders import Nominatim

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors


print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    folium-0.5.0               |             py_0          45 KB  conda-forge
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    branca-0.4.1               |             py_0          26 KB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    certifi-2020.6.20          |   py36h9f0ad1d_0         151 KB  conda-forge
    ca-certificates-2020.6.20  |       hecda079_0         145 KB  conda-forge
    openssl-1.1.1g             |       h516909a_1         2.1 MB  conda-forge
    altair-4.1.0               |             py_1         614 KB  conda-forge
    ------------------------------------------------------------
                       

### (2) Scrape data from Wikipedia table into Pandas Dataframe

In [3]:
# send the GET request
List_url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
source = requests.get(List_url).text

In [4]:
# parse data from the html into a beautifulsoup object
soup = BeautifulSoup(source, 'xml')

In [5]:
table=soup.find('table')

In [6]:
#build the dataframe such that the columns consist of PostalCode, Borough, and Neighborhood
column_names = ['Postalcode','Borough','Neighborhood']
df = pd.DataFrame(columns = column_names)

In [7]:
# Search the table for all postcode, borough, neighborhood 
for tr_cell in table.find_all('tr'):
    row_data=[]
    for td_cell in tr_cell.find_all('td'):
        row_data.append(td_cell.text.strip())
    if len(row_data)==3:
        df.loc[len(df)] = row_data

In [8]:
df.head()

Postalcode           Borough               Neighborhood
0        M1A      Not assigned               Not assigned
1        M2A      Not assigned               Not assigned
2        M3A        North York                  Parkwoods
3        M4A        North York           Victoria Village
4        M5A  Downtown Toronto  Regent Park, Harbourfront

### (3) Data Wrangling such that "Not assigned" Boroughs are removed

In [9]:
df=df[df['Borough']!='Not assigned']

In [10]:
df[df['Neighborhood']=='Not assigned']=df['Borough']
df.head()

ValueError: cannot set using a list-like indexer with a different length than the value

In [11]:
df.head()

Postalcode           Borough                                 Neighborhood
2        M3A        North York                                    Parkwoods
3        M4A        North York                             Victoria Village
4        M5A  Downtown Toronto                    Regent Park, Harbourfront
5        M6A        North York             Lawrence Manor, Lawrence Heights
6        M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [12]:
# create temporary dataframe
temp_df=df.groupby('Postalcode')['Neighborhood'].apply(lambda x: "%s" % ', '.join(x))
temp_df=temp_df.reset_index(drop=False)
temp_df.rename(columns={'Neighborhood':'Neighborhood_joined'},inplace=True)

In [13]:
#merge dataframes such that tabel excludes Borough, Neighborhood = "Not assigned"
df_merge = pd.merge(df, temp_df, on='Postalcode')

In [14]:
df_merge.drop(['Neighborhood'],axis=1,inplace=True)

In [15]:
df_merge.drop_duplicates(inplace=True)

In [16]:
df_merge.rename(columns={'Neighborhood_joined':'Neighborhood'},inplace=True)

In [17]:
df_merge.head()

Postalcode           Borough                                 Neighborhood
0        M3A        North York                                    Parkwoods
1        M4A        North York                             Victoria Village
2        M5A  Downtown Toronto                    Regent Park, Harbourfront
3        M6A        North York             Lawrence Manor, Lawrence Heights
4        M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [18]:
df_merge.shape

(103, 3)

### (4) Retrieve the Geographical Coordinates and merge Latitude/Longitude with Existing Data

In [19]:
# define a function to get coordinates
def get_geocode(postal_code):
    # initialize the variable to None
    lat_lng_coords = None
    while(lat_lng_coords is None):
        g = geocoder.google('{}, Toronto, Ontario'.format(postal_code))
        lat_lng_coords = g.latlng
    latitude = lat_lng_coords[0]
    longitude = lat_lng_coords[1]
    return latitude,longitude

In [20]:
geo_df=pd.read_csv('http://cocl.us/Geospatial_data')

In [21]:
geo_df.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [22]:
# merge the coordinates into the original dataframe
geo_df.rename(columns={'Postal Code':'Postalcode'},inplace=True)
geo_merged = pd.merge(geo_df, df_merge, on='Postalcode')

In [23]:
geo_data=geo_merged[['Postalcode','Borough','Neighborhood','Latitude','Longitude']]

In [24]:
geo_data.head()

Postalcode      Borough                            Neighborhood   Latitude  \
0        M1B  Scarborough                          Malvern, Rouge  43.806686   
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.784535   
2        M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3        M1G  Scarborough                                  Woburn  43.770992   
4        M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [25]:
# view neighborhoods and the coordinates
geo_merged.head()

Postalcode   Latitude  Longitude      Borough  \
0        M1B  43.806686 -79.194353  Scarborough   
1        M1C  43.784535 -79.160497  Scarborough   
2        M1E  43.763573 -79.188711  Scarborough   
3        M1G  43.770992 -79.216917  Scarborough   
4        M1H  43.773136 -79.239476  Scarborough   

                             Neighborhood  
0                          Malvern, Rouge  
1  Rouge Hill, Port Union, Highland Creek  
2       Guildwood, Morningside, West Hill  
3                                  Woburn  
4                               Cedarbrae

In [26]:
toronto_data=geo_data[geo_data['Borough'].str.contains("Toronto")]
toronto_data.head()

Postalcode          Borough                    Neighborhood   Latitude  \
37        M4E     East Toronto                     The Beaches  43.676357   
41        M4K     East Toronto    The Danforth West, Riverdale  43.679557   
42        M4L     East Toronto  India Bazaar, The Beaches West  43.668999   
43        M4M     East Toronto                 Studio District  43.659526   
44        M4N  Central Toronto                   Lawrence Park  43.728020   

    Longitude  
37 -79.293031  
41 -79.352188  
42 -79.315572  
43 -79.340923  
44 -79.388790

### (5) Use Foursquare API to explore Neigborhoods

In [27]:
# define Foursquare Credentials and Version
CLIENT_ID = '5MP35Q4TLOXEYHXYJSQHWOW22XWKDNUXKY30GGGC23A33X5A' # your Foursquare ID
CLIENT_SECRET = 'OARBMDID312LSWW5K5IGL1JSHZ0H3Q0BOXIN2FECEETXYORX' # your Foursquare Secret
VERSION = '20200812' # Foursquare API version

print('Your Credentials:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your Credentials:
CLIENT_ID: 5MP35Q4TLOXEYHXYJSQHWOW22XWKDNUXKY30GGGC23A33X5A
CLIENT_SECRET:OARBMDID312LSWW5K5IGL1JSHZ0H3Q0BOXIN2FECEETXYORX


In [28]:
# Retrieve top 100 venues within raidus of 500 meters
def getNearbyVenues(names, latitudes, longitudes):
    radius=500
    LIMIT=100
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])
        
    # convert the venues list into a new DataFrame
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    # define the column names
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [29]:
toronto_venues = getNearbyVenues(names=toronto_data['Neighborhood'],
                                   latitudes=toronto_data['Latitude'],
                                   longitudes=toronto_data['Longitude'])

The Beaches
The Danforth West, Riverdale
India Bazaar, The Beaches West
Studio District
Lawrence Park
Davisville North
North Toronto West,  Lawrence Park
Davisville
Moore Park, Summerhill East
Summerhill West, Rathnelly, South Hill, Forest Hill SE, Deer Park
Rosedale
St. James Town, Cabbagetown
Church and Wellesley
Regent Park, Harbourfront
Garden District, Ryerson
St. James Town
Berczy Park
Central Bay Street
Richmond, Adelaide, King
Harbourfront East, Union Station, Toronto Islands
Toronto Dominion Centre, Design Exchange
Commerce Court, Victoria Hotel
Roselawn
Forest Hill North & West, Forest Hill Road Park
The Annex, North Midtown, Yorkville
University of Toronto, Harbord
Kensington Market, Chinatown, Grange Park
CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport
Stn A PO Boxes
First Canadian Place, Underground city
Christie
Dufferin, Dovercourt Village
Little Portugal, Trinity
Brockton, Parkdale Village, Exhibition Place
High

In [30]:
toronto_venues = getNearbyVenues(names=toronto_data['Neighborhood'],
                                   latitudes=toronto_data['Latitude'],
                                   longitudes=toronto_data['Longitude'])

The Beaches
The Danforth West, Riverdale
India Bazaar, The Beaches West
Studio District
Lawrence Park
Davisville North
North Toronto West,  Lawrence Park
Davisville
Moore Park, Summerhill East
Summerhill West, Rathnelly, South Hill, Forest Hill SE, Deer Park
Rosedale
St. James Town, Cabbagetown
Church and Wellesley
Regent Park, Harbourfront
Garden District, Ryerson
St. James Town
Berczy Park
Central Bay Street
Richmond, Adelaide, King
Harbourfront East, Union Station, Toronto Islands
Toronto Dominion Centre, Design Exchange
Commerce Court, Victoria Hotel
Roselawn
Forest Hill North & West, Forest Hill Road Park
The Annex, North Midtown, Yorkville
University of Toronto, Harbord
Kensington Market, Chinatown, Grange Park
CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport
Stn A PO Boxes
First Canadian Place, Underground city
Christie
Dufferin, Dovercourt Village
Little Portugal, Trinity
Brockton, Parkdale Village, Exhibition Place
High

In [31]:
toronto_venues.head()

Neighborhood  Neighborhood Latitude  \
0                   The Beaches              43.676357   
1                   The Beaches              43.676357   
2                   The Beaches              43.676357   
3                   The Beaches              43.676357   
4  The Danforth West, Riverdale              43.679557   

   Neighborhood Longitude                               Venue  Venue Latitude  \
0              -79.293031                   Glen Manor Ravine       43.676821   
1              -79.293031  The Big Carrot Natural Food Market       43.678879   
2              -79.293031                 Grover Pub and Grub       43.679181   
3              -79.293031                       Upper Beaches       43.680563   
4              -79.352188                       MenEssentials       43.677820   

   Venue Longitude     Venue Category  
0       -79.293942              Trail  
1       -79.297734  Health Food Store  
2       -79.297215                Pub  
3       -79.292869       Neighborhood  
4       -79.351265     Cosmetics Shop

In [32]:
#Determine number of venues returned per neighborhood
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Berczy Park                                                            60   
Brockton, Parkdale Village, Exhibition Place                           26   
Business reply mail Processing Centre, South Ce...                     18   
CN Tower, King and Spadina, Railway Lands, Harb...                     17   
Central Bay Street                                                     64   
Christie                                                               17   
Church and Wellesley                                                   77   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             34   
Davisville North                                                       10   
Dufferin, Dovercourt Village                                           15   
First Canadian Place, Underground city                                100   
Forest Hill North & West, Forest Hill Road Park                         4   
Garden District, Ryerson                                              100   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          24   
India Bazaar, The Beaches West                                         20   
Kensington Market, Chinatown, Grange Park                              65   
Lawrence Park                                                           4   
Little Portugal, Trinity                                               46   
Moore Park, Summerhill East                                             4   
North Toronto West,  Lawrence Park                                     17   
Parkdale, Roncesvalles                                                 14   
Queen's Park, Ontario Provincial Government                            34   
Regent Park, Harbourfront                                              45   
Richmond, Adelaide, King                                              100   
Rosedale                                                                4   
Roselawn                                                                2   
Runnymede, Swansea                                                     39   
St. James Town                                                         87   
St. James Town, Cabbagetown                                            40   
Stn A PO Boxes                                                         97   
Studio District                                                        40   
Summerhill West, Rathnelly, South Hill, Forest ...                     17   
The Annex, North Midtown, Yorkville                                    20   
The Beaches                                                             4   
The Danforth West, Riverdale                                           41   
Toronto Dominion Centre, Design Exchange                              100   
University of Toronto, Harbord                                         34   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Berczy Park                                                             60   
Brockton, Parkdale Village, Exhibition Place                            26   
Business reply mail Processing Centre, South Ce...                      18   
CN Tower, King and Spadina, Railway Lands, Harb...                      17   
Central Bay Street                                                      64   
Christie                                                                17   
Church and Wellesley                                                    77   
Commerce Court, Victoria Hotel                                         100   
Davisville                                                              34   
Davisville North                    

In [33]:
#Determine number of unique categoriescurated for all returned venues
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 238 uniques categories.


In [34]:
# print out the list of categories
toronto_venues['Venue Category'].unique()[:50]

array(['Trail', 'Health Food Store', 'Pub', 'Neighborhood',
       'Cosmetics Shop', 'Ice Cream Shop', 'Greek Restaurant',
       'Italian Restaurant', 'Brewery', 'Juice Bar', 'Yoga Studio',
       'Fruit & Vegetable Store', 'Dessert Shop', 'Pizza Place',
       'Restaurant', 'Bookstore', 'Furniture / Home Store',
       'Grocery Store', 'Café', 'Spa', 'Bubble Tea Shop', 'Coffee Shop',
       'Bakery', 'Caribbean Restaurant', 'Indian Restaurant',
       'American Restaurant', 'Frozen Yogurt Shop', 'Lounge',
       'Liquor Store', 'Gym', 'Fish & Chips Shop', 'Sushi Restaurant',
       'Fast Food Restaurant', 'Park', 'Burrito Place', 'Pet Store',
       'Steakhouse', 'Movie Theater', 'Sandwich Place',
       'Food & Drink Shop', 'Fish Market', 'Seafood Restaurant',
       'Gay Bar', 'Cheese Shop', 'Middle Eastern Restaurant',
       'Stationery Store', 'Comfort Food Restaurant', 'Thai Restaurant',
       'Coworking Space', 'Wine Bar'], dtype=object)

In [35]:
# check if the results contain "Gym"
"Neighborhood" in toronto_venues['Venue Category'].unique()

True

### (6) Analyze Each Neighborhood

In [36]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")
toronto_onehot.drop(['Neighborhood'],axis=1,inplace=True) 
# add neighborhood column back to dataframe
toronto_onehot.insert(loc=0, column='Neighborhood', value=toronto_venues['Neighborhood'] )
print(toronto_onehot.shape)
toronto_onehot.head()

(1640, 238)


Neighborhood  Afghan Restaurant  Airport  \
0                   The Beaches                  0        0   
1                   The Beaches                  0        0   
2                   The Beaches                  0        0   
3                   The Beaches                  0        0   
4  The Danforth West, Riverdale                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0              0          0           0           0       0     0    0   
1              0          0           0           0       0     0    0   
2              0          0           0           0       0     0    0   
3              0          0           0           0       0     0    0   
4              0          0           0           0       0     0    0   

   Baseball Stadium  Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  \
0                 0                   0      0                0         0   
1                 0                   0      0                0         0   
2                 0                   0      0                0         0   
3                 0                   0      0                0         0   
4                 0                   0      0                0         0   

   Beer Store  Belgian Restaurant  Bistro  Boat or Ferry  Bookstore  Boutique  \
0           0                   0       0              0          0         0   
1           0                   0       0              0          0         0   
2           0                   0       0              0          0         0   
3           0                   0       0              0          0         0   
4           0                   0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bubble Tea Shop  Building  \
0                     0               0        0                0         0   
1                     0               0        0                0         0   
2                     0               0        0                0         0   
3                     0               0        0                0         0   
4                     0               0        0                0         0   

   Burger Joint  Burrito Place  Bus Line  Butcher  Cafeteria  Café  \
0             0              0         0        0          0     0   
1             0              0         0        0          0     0   
2             0              0         0        0          0     0   
3             0              0         0        0          0     0   
4             0              0         0   

In [37]:
#Group rows by neighborhoods and by mean frequency of occurence per category
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
print(toronto_grouped.shape)
toronto_grouped.head()

(39, 238)


Neighborhood  Afghan Restaurant  \
0                                        Berczy Park                0.0   
1       Brockton, Parkdale Village, Exhibition Place                0.0   
2  Business reply mail Processing Centre, South C...                0.0   
3  CN Tower, King and Spadina, Railway Lands, Har...                0.0   
4                                 Central Bay Street                0.0   

    Airport  Airport Food Court  Airport Gate  Airport Lounge  \
0  0.000000            0.000000      0.000000        0.000000   
1  0.000000            0.000000      0.000000        0.000000   
2  0.000000            0.000000      0.000000        0.000000   
3  0.058824            0.058824      0.058824        0.117647   
4  0.000000            0.000000      0.000000        0.000000   

   Airport Service  Airport Terminal  American Restaurant  Antique Shop  \
0         0.000000          0.000000                  0.0           0.0   
1         0.000000          0.000000                  0.0           0.0   
2         0.000000          0.000000                  0.0           0.0   
3         0.176471          0.058824                  0.0           0.0   
4         0.000000          0.000000                  0.0           0.0   

   Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0       0.0     0.016667    0.000000                  0.0               0.0   
1       0.0     0.000000    0.000000                  0.0               0.0   
2       0.0     0.000000    0.000000                  0.0               0.0   
3       0.0     0.000000    0.000000                  0.0               0.0   
4       0.0     0.000000    0.015625                  0.0               0.0   

   Athletics & Sports  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  \
0                 0.0       0.000000   0.016667         0.0    0.016667   
1                 0.0       0.000000   0.000000         0.0    0.000000   
2                 0.0       0.055556   0.000000         0.0    0.000000   
3                 0.0       0.000000   0.000000         0.0    0.000000   
4                 0.0       0.000000   0.000000         0.0    0.000000   

     Bakery  Bank       Bar  Baseball Stadium  Basketball Stadium     Beach  \
0  0.033333   0.0  0.000000               0.0            0.016667  0.016667   
1  0.076923   0.0  0.038462               0.0            0.000000  0.000000   
2  0.000000   0.0  0.000000               0.0            0.000000  0.000000   
3  0.000000   0.0  0.058824               0.0            0.000000  0.000000   
4  0.000000   0.0  0.015625               0.0            0.000000  0.000000   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant    Bistro  \
0              0.0  0.033333         0.0                 0.0  0.016667   
1              0.0  0.000000         0.0                 0.0  0.000000   
2              0.0  0.000000         0.0                 0.0  0.000000   
3              0.0  0.000000         0.0                 0.0  0.000000   
4              0.0  0.000000         0.0                 0.0  0.000000   

   Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  \
0       0.000000        0.0  0.000000                   0.0        0.016667   
1       0.000000        0.0  0.000000                   0.0        0.076923   
2       0.000000        0.0  0.000000                   0.0        0.000000   
3       0.058824        0.0  0.058824                   0.0        0.000000   
4       0.000000        0.0  0.000000                   0.0        0.000000   

    Brewery  Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0  0.000000          0.00000       0.0       0.00000       0.000000       0.0   
1  0.000000          0.00000       0.0       0.00000       0.038462       0.0   
2  0.055556          0.00000       0.0       0.00000       0.055556       0.0   
3  0.000000          0.00000       0.0       0.00000       0.000000       0.0   
4  0.000000          

In [38]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [39]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Berczy Park           Coffee Shop   
1       Brockton, Parkdale Village, Exhibition Place                  Café   
2  Business reply mail Processing Centre, South C...    Light Rail Station   
3  CN Tower, King and Spadina, Railway Lands, Har...       Airport Service   
4                                 Central Bay Street           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue  4th Most Common Venue  \
0    Seafood Restaurant           Cheese Shop         Farmers Market   
1                Bakery        Breakfast Spot  Performing Arts Venue   
2         Auto Workshop                  Park             Comic Shop   
3        Airport Lounge              Boutique        Harbor / Marina   
4        Sandwich Place                  Café     Italian Restaurant   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0                Bakery            Restaurant                  Café   
1           Coffee Shop           Yoga Studio                   Gym   
2           Pizza Place      Recording Studio            Restaurant   
3   Rental Car Location                 Plane           Coffee Shop   
4      Department Store   Japanese Restaurant          Burger Joint   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0              Beer Bar          Cocktail Bar       Department Store  
1             Pet Store             Nightclub     Italian Restaurant  
2               Butcher         Burrito Place                Brewery  
3         Boat or Ferry                   Bar       Sculpture Garden  
4       Bubble Tea Shop           Salad Place  Portuguese Restaurant

In [40]:
len(toronto_grouped[toronto_grouped["Gym"] > 0])

14

In [41]:
#Create New Dataframe for Gym data only

In [42]:
toronto_gym = toronto_grouped[["Neighborhood","Gym"]]

In [43]:
toronto_gym

Neighborhood       Gym
0                                         Berczy Park  0.016667
1        Brockton, Parkdale Village, Exhibition Place  0.038462
2   Business reply mail Processing Centre, South C...  0.000000
3   CN Tower, King and Spadina, Railway Lands, Har...  0.000000
4                                  Central Bay Street  0.000000
5                                            Christie  0.000000
6                                Church and Wellesley  0.000000
7                      Commerce Court, Victoria Hotel  0.040000
8                                          Davisville  0.058824
9                                    Davisville North  0.100000
10                       Dufferin, Dovercourt Village  0.000000
11             First Canadian Place, Underground city  0.040000
12    Forest Hill North & West, Forest Hill Road Park  0.000000
13                           Garden District, Ryerson  0.010000
14  Harbourfront East, Union Station, Toronto Islands  0.000000
15                      High Park, The Junction South  0.000000
16                     India Bazaar, The Beaches West  0.050000
17          Kensington Market, Chinatown, Grange Park  0.000000
18                                      Lawrence Park  0.000000
19                           Little Portugal, Trinity  0.000000
20                        Moore Park, Summerhill East  0.000000
21                 North Toronto West,  Lawrence Park  0.000000
22                             Parkdale, Roncesvalles  0.000000
23        Queen's Park, Ontario Provincial Government  0.029412
24                          Regent Park, Harbourfront  0.000000
25                           Richmond, Adelaide, King  0.040000
26                                           Rosedale  0.000000
27                                           Roselawn  0.000000
28                                 Runnymede, Swansea  0.025641
29                                     St. James Town  0.022989
30                        St. James Town, Cabbagetown  0.000000
31                                     Stn A PO Boxes  0.030928
32                                    Studio District  0.000000
33  Summerhill West, Rathnelly, South Hill, Forest...  0.000000
34                The Annex, North Midtown, Yorkville  0.000000
35                                        The Beaches  0.000000
36                       The Danforth West, Riverdale  0.000000
37           Toronto Dominion Centre, Design Exchange  0.010000
38                     University of Toronto, Harbord  0.000000

### (7) Cluster the Neighborhoods

In [44]:
# set number of clusters
kclusters = 5

toronto_gym_clustering = toronto_gym.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_gym_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 3, 1, 1, 1, 1, 1, 3, 4, 2], dtype=int32)

In [46]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood
toronto_merged = toronto_gym.copy()

# add cluster labels
toronto_merged["Cluster Labels"] = kmeans.labels_

toronto_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
toronto_merged.head()


Neighborhood       Gym  Cluster Labels
0                                        Berczy Park  0.016667               0
1       Brockton, Parkdale Village, Exhibition Place  0.038462               3
2  Business reply mail Processing Centre, South C...  0.000000               1
3  CN Tower, King and Spadina, Railway Lands, Har...  0.000000               1
4                                 Central Bay Street  0.000000               1

In [49]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(toronto_venues.set_index('Neighborhood'), on='Neighborhood')

print(toronto_merged.shape)
toronto_merged.head() # check the last columns!

(1640, 19)


Neighborhood       Gym  Cluster Labels 1st Most Common Venue  \
0  Berczy Park  0.016667               0           Coffee Shop   
0  Berczy Park  0.016667               0           Coffee Shop   
0  Berczy Park  0.016667               0           Coffee Shop   
0  Berczy Park  0.016667               0           Coffee Shop   
0  Berczy Park  0.016667               0           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0    Seafood Restaurant           Cheese Shop        Farmers Market   
0    Seafood Restaurant           Cheese Shop        Farmers Market   
0    Seafood Restaurant           Cheese Shop        Farmers Market   
0    Seafood Restaurant           Cheese Shop        Farmers Market   
0    Seafood Restaurant           Cheese Shop        Farmers Market   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0                Bakery            Restaurant                  Café   
0                Bakery            Restaurant                  Café   
0                Bakery            Restaurant                  Café   
0                Bakery            Restaurant                  Café   
0                Bakery            Restaurant                  Café   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
0              Beer Bar          Cocktail Bar       Department Store   
0              Beer Bar          Cocktail Bar       Department Store   
0              Beer Bar          Cocktail Bar       Department Store   
0              Beer Bar          Cocktail Bar       Department Store   
0              Beer Bar          Cocktail Bar       Department Store   

   Neighborhood Latitude  Neighborhood Longitude  \
0              43.644771              -79.373306   
0              43.644771              -79.373306   
0              43.644771              -79.373306   
0              43.644771              -79.373306   
0              43.644771              -79.373306   

                                  Venue  Venue Latitude  Venue Longitude  \
0  The Keg Steakhouse + Bar - Esplanade       43.646712       -79.374768   
0                                  LCBO       43.642944       -79.372440   
0                        Fresh On Front       43.647815       -79.374453   
0                         Meridian Hall       43.646292       -79.376022   
0                Goose Island Brewhouse       43.647329       -79.373541   

                  Venue Category  
0                     Restaurant  
0                   Liquor Store  
0  Vegetarian / Vegan Restaurant  
0                   Concert Hall  
0                       Beer Bar

In [50]:
# sort the results by Cluster Labels
print(toronto_merged.shape)
toronto_merged.sort_values(["Cluster Labels"], inplace=True)
toronto_merged

(1640, 19)


Neighborhood       Gym  \
0                                         Berczy Park  0.016667   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
31                                     Stn A PO Boxes  0.030928   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                                     St. James Town  0.022989   
29                   

In [52]:
#Visualize the resulting clusters
address = 'Toronto, CA'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [55]:
#Generate the map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Venue Latitude'], toronto_merged['Venue Longitude'], toronto_merged['Venue'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### (8) Examine each Cluster

In [56]:
# Cluster Zero
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0]

Neighborhood       Gym  Cluster Labels  \
0                                   Berczy Park  0.016667               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
31                               Stn A PO Boxes  0.030928               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                               St. James Town  0.022989               0   
29                             

In [57]:
#Cluster one
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1]

Neighborhood   Gym  Cluster Labels  \
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
33  Summerhill West, Rathnelly, South Hill, Forest...  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
27                                           Roselawn  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
38                     University of Toronto, Harbord  0.00               1   
27                                           Roselawn  0.00               1   
26                                           Rosedale  0.00               1   
26                                           Rosedale  0.00               1   
26                                           Rosedale  0.00               1   
24                          Regent Park, Harbourfront  0.00               1   
24          

In [58]:
#Cluster two
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2]

Neighborhood  Gym  Cluster Labels 1st Most Common Venue  \
9  Davisville North  0.1               2  Gym / Fitness Center   
9  Davisville North  0.1               2  Gym / Fitness Center   
9  Davisville North  0.1               2  Gym / Fitness Center   
9  Davisville North  0.1               2  Gym / Fitness Center   
9  Davisville North  0.1               2  Gym / Fitness Center   
9  Davisville North  0.1               2  Gym / Fitness Center   
9  Davisville North  0.1               2  Gym / Fitness Center   
9  Davisville North  0.1               2  Gym / Fitness Center   
9  Davisville North  0.1               2  Gym / Fitness Center   
9  Davisville North  0.1               2  Gym / Fitness Center   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
9                 Hotel        Breakfast Spot     Food & Drink Shop   
9                 Hotel        Breakfast Spot     Food & Drink Shop   
9                 Hotel        Breakfast Spot     Food & Drink Shop   
9                 Hotel        Breakfast Spot     Food & Drink Shop   
9                 Hotel        Breakfast Spot     Food & Drink Shop   
9                 Hotel        Breakfast Spot     Food & Drink Shop   
9                 Hotel        Breakfast Spot     Food & Drink Shop   
9                 Hotel        Breakfast Spot     Food & Drink Shop   
9                 Hotel        Breakfast Spot     Food & Drink Shop   
9                 Hotel        Breakfast Spot     Food & Drink Shop   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
9        Sandwich Place      Department Store          Dance Studio   
9        Sandwich Place      Department Store          Dance Studio   
9        Sandwich Place      Department Store          Dance Studio   
9        Sandwich Place      Department Store          Dance Studio   
9        Sandwich Place      Department Store          Dance Studio   
9        Sandwich Place      Department Store          Dance Studio   
9        Sandwich Place      Department Store          Dance Studio   
9        Sandwich Place      Department Store          Dance Studio   
9        Sandwich Place      Department Store          Dance Studio   
9        Sandwich Place      Department Store          Dance Studio   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
9                   Gym                  Park            Pizza Place   
9                   Gym                  Park            Pizza Place   
9                   Gym                  Park            Pizza Place   
9                   Gym                  Park            Pizza Place   
9                   Gym                  Park            Pizza Place   
9                   Gym                  Park            Pizza Place   
9                   Gym                  Park            Pizza Place   
9                   Gym                  Park            Pizza Place   
9                   Gym                  Park            Pizza Place   
9                   Gym                  Park            Pizza Place   

   Neighborhood Latitude  Neighborhood Longitude  \
9              43.712751              -79.390197   
9              43.712751              -79.390197   
9              43.712751              -79.390197   
9              43.712751              -79.390197   
9              43.712751              -79.390197   
9              43.712751              -79.390197   
9              43.712751              -79.390197   
9              43.712751              -79.390197   
9              43.712751              -79.390197   
9              43.712751              -79.390197   

                                    Venue  Venue Latitude  Venue Longitude  \
9                                  Subway       43.708474       -79.390674   
9                           Sherwood Park       43.716551       -79.387776   
9      900 Mount Pleasant - Residents Gym       43.711671       -79.391767   
9  Best Western Roehampton Hotel & Sui

In [59]:
#Cluster three
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3]

Neighborhood       Gym  Cluster Labels  \
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
25                      Richmond, Adelaide, King  0.040000               3   
7                 Commerce Court, Victoria Hotel  0.040000               3   
1   Brockton, Parkdale Village, Exhibition Place  0.038462               3   
1   Brockton, Parkdale Village, Exhibition Place  0.038462               3   
1   Brockton, Parkdale Village, Exhibition Place  0.038462               3   
1   Brockton, Parkdale Village, Exhibition Place  0.038462

In [60]:
#Cluster four
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4]

Neighborhood       Gym  Cluster Labels  \
16  India Bazaar, The Beaches West  0.050000               4   
16  India Bazaar, The Beaches West  0.050000               4   
16  India Bazaar, The Beaches West  0.050000               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
16  India Bazaar, The Beaches West  0.050000               4   
8                       Davisville  0.058824               4   
16  India Bazaar, The Beaches West  0.050000               4   
16  India Bazaar, The Beaches West  0.050000               4   
16  India Bazaar, The Beaches West  0.050000               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
16  India Bazaar, The Beaches West  0.050000               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
16  India Bazaar, The Beaches West  0.050000               4   
16  India Bazaar, The Beaches West  0.050000               4   
16  India Bazaar, The Beaches West  0.050000               4   
16  India Bazaar, The Beaches West  0.050000               4   
16  India Bazaar, The Beaches West  0.050000               4   
16  India Bazaar, The Beaches West  0.050000               4   
16  India Bazaar, The Beaches West  0.050000               4   
16  India Bazaar, The Beaches West  0.050000               4   
8                       Davisville  0.058824               4   
16  India Bazaar, The Beaches West  0.050000               4   
16  India Bazaar, The Beaches West  0.050000               4   
16  India Bazaar, The Beaches West  0.050000               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
8                       Davisville  0.058824               4   
16  India Bazaar, The Beaches West  0.050000               4   
8                       Davisville  0.058824               4   

   1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
16        Sandwich Place           Pizza Place     Food & Drink Shop   
16        Sandwich Place           Pizza Place     Food & Drink Shop   
16        Sandwich Place           Pizza Place     Food & Drink Shop   
8         Sandwich Place          Dessert Shop           Pizza Place   
8         Sandwich Place          Dessert Shop           Pizza Place   
8         Sandwich Place          Dessert Shop           Pizza Place 

## Observations 

By K-means clustering we have elucidated five clusters, distinguished from another by density of “Gyms”.

Cluster 0: Low Gym Density

Cluster 1: No Gym Density

Cluster 2: High Gym Density

Cluster 3: Low- Moderate Gym Density

Cluster 4: Moderate Gym Density

We see that cluster 0 and cluster 1 have the lowest density of gyms, thus these clusters may represent a population of peoples currently underserved in the domain of fitness & health.  In contrast, cluster 2 has the highest density of gyms and may be saturated by over-supply.  Further analysis is required to identify those contributing factors which may inform the low occurrence of gyms in cluster 0 and cluster 1 in contrast to the oversaturation of gyms in cluster 2.  Limitations include the use of one factor, i.e. the density of gyms in the area.  Factors such as median household income, demography information such as age, characterization of the cluster as residential, business, or other may provide further guidance to real estate developers and those interested in developing gyms and wellness centers.  Based on this study, cluster 0 and cluster 1 would benefit greatly from the introduction of a gym or wellness center and should be the focus of future development.